# Priming neural networks with an appropriate initializer.

In this quick experiment, we will be testing the effect of different weight/bias initializations on a very simple variational autoencoder (VAE). We will be using the MNIST dataset to prototype. The VAE will essentially have 3 layes:
- an input layer of shape (784) that would represent a flattened MNIST image (28,28).
- a single hidden layer where the input will be "encoded" down from 784 features to 32.
- an output layer that "decodes" the hidden latent representation back into a MNIST image.

In [59]:
import numpy as np
import tensorflow as tf
import plotly
from tensorflow.examples.tutorials.mnist import input_data
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)
from plotly import tools
print ("tensorflow {}".format(tf.__version__))
print ("plotly {}".format(plotly.__version__))

tensorflow 1.4.1
plotly 2.2.3


## import data

In [60]:
mnist = input_data.read_data_sets('MNIST_data', validation_size=0)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


## set various initializations

Here we pick 8 different tensorflow initializations to test.

In [61]:
initializers = [
# we start with the no brainer zeros and ones and constants
{"type":tf.zeros_initializer(), "name":"zeros"},
{"type":tf.ones_initializer(), "name":"ones"},
    
# random distributions
{"type":tf.random_normal_initializer(mean=0.0,stddev=1.0), "name":"random_normal"},
{"type":tf.random_uniform_initializer(minval=0,maxval=1.0), "name":"random_uniform"},
    
# glorot or Xavier initalizations
{"type":tf.glorot_normal_initializer(), "name":"glorot_normal"},
{"type":tf.glorot_uniform_initializer(), "name":"glorot_uniform"},
    
# others
{"type":tf.orthogonal_initializer(gain=1.0), "name":"orthogonal"},
{"type":tf.initializers.identity(gain=1.0), "name":"identity"}  
]

# add a loss list and value list to each entry in the list
for entry in initializers:
    entry["loss"] = [] 
    entry["value"] = [] 

## visualize initialization distributions

We will run generate square 2d tensors of shape 100*100 from each initalizer and plot their distribution, just to get an idea about how tensorflow samples them.

In [62]:
tensor_dim_0 = 100
tensor_dim_1 = 100

In [63]:
# set initializer value
for initializer in initializers:
    tf.reset_default_graph()
    with tf.Graph().as_default():
        # set seed
        tf.set_random_seed(42)
        # set dummy variable
        var = tf.Variable(initial_value=tf.get_variable(shape=[tensor_dim_0,tensor_dim_1],
                                                        name = initializer['name'],
                                                        initializer=initializer['type']))
        sess = tf.Session()
        init = tf.global_variables_initializer()
        sess.run(init)
        initializer['value'] = sess.run(var)

In [64]:
# plot distributions
# make figure
fig = tools.make_subplots(rows=4, cols=2, subplot_titles=[x['name'] for x in initializers])
for idx,initializer in enumerate(initializers):
    # make trace
    x = np.reshape(initializer['value'],tensor_dim_0*tensor_dim_1)
    trace = go.Histogram(x=x,histnorm='',opacity=0.6)
    fig.append_trace(trace, (idx//2) + 1, (idx%2) + 1 )

    
fig['layout'].update(height=1200, 
                     width=1000, 
                     showlegend=False, 
                     title='Tensorflow initializer distribution - 10k samples',
                    font=dict(size=12))
iplot(fig) 
plot(fig,
     show_link=False,
     image_height=1200, 
     image_width=1000, 
     image_filename="histograms", 
     image="svg")

This is the format of your plot grid:
[ (1,1) x1,y1 ]  [ (1,2) x2,y2 ]
[ (2,1) x3,y3 ]  [ (2,2) x4,y4 ]
[ (3,1) x5,y5 ]  [ (3,2) x6,y6 ]
[ (4,1) x7,y7 ]  [ (4,2) x8,y8 ]



'file:///home/ahmed/Dropbox/medium/yhat/00000_priming_neural_networks_with_an appropriate_initializer/temp-plot.html'

## sanity check for the glorot initializers

Here, we will be manually calculating the statistcs of the glorot intializers. We will then compare that to the standard deviation of the values tensorflow gave us above. For the glorot_normal, we will check the standard deviation. For the glorot_uniform, we will check the limits. All looks good!

In [65]:
# from tensorflow - https://www.tensorflow.org/api_docs/python/tf/glorot_normal_initializer
# stddev = sqrt(2 / (fan_in + fan_out))
stddev_calculated = np.sqrt(2 / (tensor_dim_0 + tensor_dim_1))
stddev_actual = np.std(np.reshape(initializers[4]['value'],100*100))
print ("glorot_normal_initializer std: " ,stddev_calculated, stddev_actual)

# from tensorflow - https://www.tensorflow.org/api_docs/python/tf/glorot_uniform_initializer
# limit = sqrt(6 / (fan_in + fan_out))
limit_calculated = np.sqrt(6 / (tensor_dim_0 + tensor_dim_1))
limit_actual = np.max(initializers[5]['value'])
print ("glorot_uniform_initializer limit: " ,limit_calculated, limit_actual)

glorot_normal_initializer std:  0.1 0.0886468
glorot_uniform_initializer limit:  0.173205080757 0.173109


## build models with different weight initalizations.

In [66]:
epochs = 10
batch_size = 200
intializers_to_use = initializers[:6] # intializers
for initializer in intializers_to_use:
    tf.reset_default_graph()
    with tf.Graph().as_default():
        # set seed
        tf.set_random_seed(42)
        hidden_size = 32 
        # set weight and bias
        # weight initalizer
        weight_initializer = tf.glorot_uniform_initializer() # initializer['type'] 
        # bias initalizer 
        bias_initializer = initializer['type'] # tf.zeros_initializer()
        weight = {
            "i_h" : tf.Variable(initial_value=tf.get_variable(shape=[784,hidden_size],
                                                name="weight_i_h",
                                                initializer=weight_initializer)), 
            "h_o" : tf.Variable(initial_value=tf.get_variable(shape=[hidden_size,784],
                                                name="weight_h_o",
                                                initializer=weight_initializer)) 
        }  
        bias = {
            "i_h" : tf.Variable(initial_value= tf.get_variable(shape=[hidden_size],
                                                name="bias_i_h",
                                                initializer=bias_initializer)),
            "h_o" : tf.Variable(initial_value= tf.get_variable(shape=[784],
                                                name="bias_h_o",
                                                initializer=bias_initializer))
        }
        # placeholders
        _inputs = tf.placeholder(dtype=tf.float32,shape=[None,784],name="input_placeholder")
        _targets = tf.placeholder(dtype=tf.float32 ,shape=[None,784],name="target_placeholder")
        # encode
        encode = tf.nn.relu( tf.nn.bias_add ( tf.matmul(_inputs,weight["i_h"]) , bias["i_h"] ) ) 
        # logits
        logits =  tf.nn.bias_add( tf.matmul(encode,weight["h_o"]), bias["h_o"]) 
        # sigmoid 
        decode = tf.nn.sigmoid(logits)
        # cross-entropy 
        loss = tf.nn.sigmoid_cross_entropy_with_logits(logits=logits,labels=_targets)
        # mean
        cost = tf.reduce_mean(loss)
        # optimizer
        opt = tf.train.AdamOptimizer(learning_rate=0.001).minimize(cost)
        # session
        sess = tf.Session()
        init = tf.global_variables_initializer()
        sess.run(init)
        # run
        for epoch in range(epochs):
            for i in range(mnist.train.num_examples//batch_size):
                batch = mnist.train.next_batch(batch_size,shuffle=False)
                feed = {_inputs:batch[0],_targets:batch[0]}
                batch_cost, _ = sess.run([ cost, opt], feed_dict=feed)
                # add to list
                initializer['loss'].append(batch_cost)
                print("Epoch: {}/{} - ".format(epoch+1, epochs),"Training loss: {:.4f}".format(batch_cost))

Epoch: 1/10 -  Training loss: 0.6945
Epoch: 1/10 -  Training loss: 0.6912
Epoch: 1/10 -  Training loss: 0.6878
Epoch: 1/10 -  Training loss: 0.6839
Epoch: 1/10 -  Training loss: 0.6794
Epoch: 1/10 -  Training loss: 0.6750
Epoch: 1/10 -  Training loss: 0.6662
Epoch: 1/10 -  Training loss: 0.6607
Epoch: 1/10 -  Training loss: 0.6534
Epoch: 1/10 -  Training loss: 0.6411
Epoch: 1/10 -  Training loss: 0.6294
Epoch: 1/10 -  Training loss: 0.6180
Epoch: 1/10 -  Training loss: 0.6020
Epoch: 1/10 -  Training loss: 0.5904
Epoch: 1/10 -  Training loss: 0.5733
Epoch: 1/10 -  Training loss: 0.5593
Epoch: 1/10 -  Training loss: 0.5405
Epoch: 1/10 -  Training loss: 0.5275
Epoch: 1/10 -  Training loss: 0.5070
Epoch: 1/10 -  Training loss: 0.4859
Epoch: 1/10 -  Training loss: 0.4678
Epoch: 1/10 -  Training loss: 0.4510
Epoch: 1/10 -  Training loss: 0.4377
Epoch: 1/10 -  Training loss: 0.4298
Epoch: 1/10 -  Training loss: 0.4114
Epoch: 1/10 -  Training loss: 0.3960
Epoch: 1/10 -  Training loss: 0.3839
E

Epoch: 1/10 -  Training loss: 0.2053
Epoch: 1/10 -  Training loss: 0.1894
Epoch: 1/10 -  Training loss: 0.2008
Epoch: 1/10 -  Training loss: 0.2018
Epoch: 1/10 -  Training loss: 0.1970
Epoch: 1/10 -  Training loss: 0.1885
Epoch: 1/10 -  Training loss: 0.1917
Epoch: 1/10 -  Training loss: 0.1998
Epoch: 1/10 -  Training loss: 0.2020
Epoch: 1/10 -  Training loss: 0.1976
Epoch: 1/10 -  Training loss: 0.1937
Epoch: 1/10 -  Training loss: 0.1990
Epoch: 1/10 -  Training loss: 0.1795
Epoch: 1/10 -  Training loss: 0.1943
Epoch: 1/10 -  Training loss: 0.1847
Epoch: 1/10 -  Training loss: 0.1961
Epoch: 1/10 -  Training loss: 0.1905
Epoch: 1/10 -  Training loss: 0.1905
Epoch: 1/10 -  Training loss: 0.1880
Epoch: 1/10 -  Training loss: 0.1928
Epoch: 1/10 -  Training loss: 0.1982
Epoch: 1/10 -  Training loss: 0.1981
Epoch: 1/10 -  Training loss: 0.1874
Epoch: 1/10 -  Training loss: 0.1913
Epoch: 1/10 -  Training loss: 0.1870
Epoch: 1/10 -  Training loss: 0.1965
Epoch: 1/10 -  Training loss: 0.1877
E

Epoch: 2/10 -  Training loss: 0.1685
Epoch: 2/10 -  Training loss: 0.1646
Epoch: 2/10 -  Training loss: 0.1695
Epoch: 2/10 -  Training loss: 0.1664
Epoch: 2/10 -  Training loss: 0.1694
Epoch: 2/10 -  Training loss: 0.1653
Epoch: 2/10 -  Training loss: 0.1743
Epoch: 2/10 -  Training loss: 0.1775
Epoch: 2/10 -  Training loss: 0.1711
Epoch: 2/10 -  Training loss: 0.1767
Epoch: 2/10 -  Training loss: 0.1782
Epoch: 2/10 -  Training loss: 0.1647
Epoch: 2/10 -  Training loss: 0.1678
Epoch: 2/10 -  Training loss: 0.1696
Epoch: 2/10 -  Training loss: 0.1765
Epoch: 2/10 -  Training loss: 0.1748
Epoch: 2/10 -  Training loss: 0.1668
Epoch: 2/10 -  Training loss: 0.1651
Epoch: 2/10 -  Training loss: 0.1681
Epoch: 2/10 -  Training loss: 0.1622
Epoch: 2/10 -  Training loss: 0.1709
Epoch: 2/10 -  Training loss: 0.1611
Epoch: 2/10 -  Training loss: 0.1571
Epoch: 2/10 -  Training loss: 0.1637
Epoch: 2/10 -  Training loss: 0.1599
Epoch: 2/10 -  Training loss: 0.1690
Epoch: 2/10 -  Training loss: 0.1723
E

Epoch: 3/10 -  Training loss: 0.1436
Epoch: 3/10 -  Training loss: 0.1559
Epoch: 3/10 -  Training loss: 0.1527
Epoch: 3/10 -  Training loss: 0.1474
Epoch: 3/10 -  Training loss: 0.1416
Epoch: 3/10 -  Training loss: 0.1366
Epoch: 3/10 -  Training loss: 0.1496
Epoch: 3/10 -  Training loss: 0.1475
Epoch: 3/10 -  Training loss: 0.1547
Epoch: 3/10 -  Training loss: 0.1475
Epoch: 3/10 -  Training loss: 0.1465
Epoch: 3/10 -  Training loss: 0.1442
Epoch: 3/10 -  Training loss: 0.1648
Epoch: 3/10 -  Training loss: 0.1481
Epoch: 3/10 -  Training loss: 0.1499
Epoch: 3/10 -  Training loss: 0.1516
Epoch: 3/10 -  Training loss: 0.1471
Epoch: 3/10 -  Training loss: 0.1510
Epoch: 3/10 -  Training loss: 0.1422
Epoch: 3/10 -  Training loss: 0.1460
Epoch: 3/10 -  Training loss: 0.1553
Epoch: 3/10 -  Training loss: 0.1515
Epoch: 3/10 -  Training loss: 0.1328
Epoch: 3/10 -  Training loss: 0.1440
Epoch: 3/10 -  Training loss: 0.1553
Epoch: 3/10 -  Training loss: 0.1423
Epoch: 3/10 -  Training loss: 0.1373
E

Epoch: 4/10 -  Training loss: 0.1346
Epoch: 4/10 -  Training loss: 0.1332
Epoch: 4/10 -  Training loss: 0.1325
Epoch: 4/10 -  Training loss: 0.1430
Epoch: 4/10 -  Training loss: 0.1396
Epoch: 4/10 -  Training loss: 0.1254
Epoch: 4/10 -  Training loss: 0.1327
Epoch: 4/10 -  Training loss: 0.1330
Epoch: 4/10 -  Training loss: 0.1372
Epoch: 4/10 -  Training loss: 0.1353
Epoch: 4/10 -  Training loss: 0.1328
Epoch: 4/10 -  Training loss: 0.1272
Epoch: 4/10 -  Training loss: 0.1649
Epoch: 4/10 -  Training loss: 0.1310
Epoch: 4/10 -  Training loss: 0.1345
Epoch: 4/10 -  Training loss: 0.1230
Epoch: 4/10 -  Training loss: 0.1258
Epoch: 4/10 -  Training loss: 0.1240
Epoch: 4/10 -  Training loss: 0.1258
Epoch: 4/10 -  Training loss: 0.1258
Epoch: 4/10 -  Training loss: 0.1259
Epoch: 4/10 -  Training loss: 0.1269
Epoch: 4/10 -  Training loss: 0.1355
Epoch: 4/10 -  Training loss: 0.1378
Epoch: 4/10 -  Training loss: 0.1394
Epoch: 4/10 -  Training loss: 0.1368
Epoch: 4/10 -  Training loss: 0.1354
E

...

Epoch: 7/10 -  Training loss: 0.1081
Epoch: 7/10 -  Training loss: 0.1066
Epoch: 7/10 -  Training loss: 0.1038
Epoch: 7/10 -  Training loss: 0.1074
Epoch: 7/10 -  Training loss: 0.1040
Epoch: 7/10 -  Training loss: 0.1050
Epoch: 7/10 -  Training loss: 0.1134
Epoch: 7/10 -  Training loss: 0.1192
Epoch: 7/10 -  Training loss: 0.1077
Epoch: 7/10 -  Training loss: 0.1006
Epoch: 7/10 -  Training loss: 0.1082
Epoch: 7/10 -  Training loss: 0.1083
Epoch: 7/10 -  Training loss: 0.1093
Epoch: 7/10 -  Training loss: 0.1037
Epoch: 7/10 -  Training loss: 0.1096
Epoch: 7/10 -  Training loss: 0.1105
Epoch: 7/10 -  Training loss: 0.1050
Epoch: 7/10 -  Training loss: 0.1087
Epoch: 7/10 -  Training loss: 0.1076
Epoch: 7/10 -  Training loss: 0.1108
Epoch: 7/10 -  Training loss: 0.1154
Epoch: 7/10 -  Training loss: 0.1063
Epoch: 7/10 -  Training loss: 0.1104
Epoch: 7/10 -  Training loss: 0.1078
Epoch: 7/10 -  Training loss: 0.1077
Epoch: 7/10 -  Training loss: 0.1107
Epoch: 7/10 -  Training loss: 0.1048
E

Epoch: 8/10 -  Training loss: 0.1092
Epoch: 8/10 -  Training loss: 0.1062
Epoch: 8/10 -  Training loss: 0.1039
Epoch: 8/10 -  Training loss: 0.1071
Epoch: 8/10 -  Training loss: 0.1022
Epoch: 8/10 -  Training loss: 0.1048
Epoch: 8/10 -  Training loss: 0.1088
Epoch: 8/10 -  Training loss: 0.1081
Epoch: 8/10 -  Training loss: 0.1053
Epoch: 8/10 -  Training loss: 0.1084
Epoch: 8/10 -  Training loss: 0.1138
Epoch: 8/10 -  Training loss: 0.1010
Epoch: 8/10 -  Training loss: 0.1053
Epoch: 8/10 -  Training loss: 0.1046
Epoch: 8/10 -  Training loss: 0.1037
Epoch: 8/10 -  Training loss: 0.1114
Epoch: 8/10 -  Training loss: 0.1022
Epoch: 8/10 -  Training loss: 0.1035
Epoch: 8/10 -  Training loss: 0.0974
Epoch: 8/10 -  Training loss: 0.0996
Epoch: 8/10 -  Training loss: 0.1054
Epoch: 8/10 -  Training loss: 0.1085
Epoch: 8/10 -  Training loss: 0.1057
Epoch: 8/10 -  Training loss: 0.1085
Epoch: 8/10 -  Training loss: 0.1090
Epoch: 8/10 -  Training loss: 0.1088
Epoch: 8/10 -  Training loss: 0.0971
E

Epoch: 9/10 -  Training loss: 0.1018
Epoch: 9/10 -  Training loss: 0.0976
Epoch: 9/10 -  Training loss: 0.1047
Epoch: 9/10 -  Training loss: 0.1036
Epoch: 9/10 -  Training loss: 0.1024
Epoch: 9/10 -  Training loss: 0.1027
Epoch: 9/10 -  Training loss: 0.0979
Epoch: 9/10 -  Training loss: 0.1009
Epoch: 9/10 -  Training loss: 0.0981
Epoch: 9/10 -  Training loss: 0.0995
Epoch: 9/10 -  Training loss: 0.0940
Epoch: 9/10 -  Training loss: 0.0973
Epoch: 9/10 -  Training loss: 0.1000
Epoch: 9/10 -  Training loss: 0.1046
Epoch: 9/10 -  Training loss: 0.1005
Epoch: 9/10 -  Training loss: 0.1087
Epoch: 9/10 -  Training loss: 0.0989
Epoch: 9/10 -  Training loss: 0.1024
Epoch: 9/10 -  Training loss: 0.1037
Epoch: 9/10 -  Training loss: 0.1002
Epoch: 9/10 -  Training loss: 0.1008
Epoch: 9/10 -  Training loss: 0.0998
Epoch: 9/10 -  Training loss: 0.1008
Epoch: 9/10 -  Training loss: 0.0959
Epoch: 9/10 -  Training loss: 0.1038
Epoch: 9/10 -  Training loss: 0.1033
Epoch: 9/10 -  Training loss: 0.1072
E

Epoch: 9/10 -  Training loss: 0.1083
Epoch: 9/10 -  Training loss: 0.1011
Epoch: 9/10 -  Training loss: 0.1073
Epoch: 9/10 -  Training loss: 0.1031
Epoch: 9/10 -  Training loss: 0.1022
Epoch: 9/10 -  Training loss: 0.0967
Epoch: 9/10 -  Training loss: 0.1016
Epoch: 9/10 -  Training loss: 0.1027
Epoch: 9/10 -  Training loss: 0.0996
Epoch: 9/10 -  Training loss: 0.0949
Epoch: 9/10 -  Training loss: 0.0963
Epoch: 9/10 -  Training loss: 0.0959
Epoch: 9/10 -  Training loss: 0.0998
Epoch: 9/10 -  Training loss: 0.1044
Epoch: 9/10 -  Training loss: 0.1016
Epoch: 9/10 -  Training loss: 0.1043
Epoch: 9/10 -  Training loss: 0.0948
Epoch: 9/10 -  Training loss: 0.0971
Epoch: 9/10 -  Training loss: 0.0961
Epoch: 9/10 -  Training loss: 0.1010
Epoch: 9/10 -  Training loss: 0.0998
Epoch: 9/10 -  Training loss: 0.0989
Epoch: 9/10 -  Training loss: 0.0980
Epoch: 9/10 -  Training loss: 0.1042
Epoch: 9/10 -  Training loss: 0.1051
Epoch: 9/10 -  Training loss: 0.1030
Epoch: 9/10 -  Training loss: 0.0975
E

Epoch: 10/10 -  Training loss: 0.0913
Epoch: 10/10 -  Training loss: 0.0984
Epoch: 10/10 -  Training loss: 0.0965
Epoch: 10/10 -  Training loss: 0.0974
Epoch: 10/10 -  Training loss: 0.0998
Epoch: 10/10 -  Training loss: 0.0964
Epoch: 10/10 -  Training loss: 0.1004
Epoch: 10/10 -  Training loss: 0.0962
Epoch: 10/10 -  Training loss: 0.0992
Epoch: 10/10 -  Training loss: 0.0972
Epoch: 10/10 -  Training loss: 0.1023
Epoch: 10/10 -  Training loss: 0.1019
Epoch: 10/10 -  Training loss: 0.1003
Epoch: 10/10 -  Training loss: 0.1019
Epoch: 10/10 -  Training loss: 0.0970
Epoch: 10/10 -  Training loss: 0.0963
Epoch: 10/10 -  Training loss: 0.0924
Epoch: 10/10 -  Training loss: 0.0979
Epoch: 10/10 -  Training loss: 0.1059
Epoch: 10/10 -  Training loss: 0.1042
Epoch: 10/10 -  Training loss: 0.0999
Epoch: 10/10 -  Training loss: 0.0997
Epoch: 10/10 -  Training loss: 0.1006
Epoch: 10/10 -  Training loss: 0.0958
Epoch: 10/10 -  Training loss: 0.1031
Epoch: 10/10 -  Training loss: 0.0969
Epoch: 10/10

## plot batch loss

In [68]:
plot_data = []
for initializer in initializers:
    trace = go.Scatter(
        x = np.arange(len(initializer['loss'])),
        y = initializer['loss'],
        name = initializer['name']
    )
    plot_data.append(trace)

layout = go.Layout(
    title = "Step loss with different biass initialization",
    xaxis=dict(
        showgrid=True,
        title="steps"
    ),
    yaxis=dict(
        showgrid=True,
        title="loss",
        range=[0,0.4]
    ),
    autosize=True,
    showlegend=True,
)

fig = go.Figure(data=plot_data, layout=layout)
iplot(fig)
plot(fig,
     show_link=False,
     image_filename="biases_0", 
     image="svg")

'file:///home/ahmed/Dropbox/medium/yhat/00000_priming_neural_networks_with_an appropriate_initializer/temp-plot.html'